In [1]:
#Dependencies
import numpy as np
import pandas as pd
import json
import requests
import psycopg2
from pprint import pprint
from pandas_profiling import ProfileReport
from sqlalchemy import create_engine
from sqlalchemy.orm import Session
from config import api_key, username, password, host, port, database

In [2]:
# Covid Act Now API
url = "https://api.covidactnow.org/v2/county/MI.json?"

# Build query URL
query_url = f"{url}apiKey={api_key}"

In [3]:
# Current data for all county in MI state
covid_19_data = requests.get(query_url).json()

pprint(covid_19_data[0])

{'actuals': {'cases': 739,
             'contactTracers': None,
             'deaths': 32,
             'hospitalBeds': {'capacity': None,
                              'currentUsageCovid': None,
                              'currentUsageTotal': None,
                              'typicalUsageRate': None},
             'icuBeds': {'capacity': None,
                         'currentUsageCovid': None,
                         'currentUsageTotal': None,
                         'typicalUsageRate': None},
             'negativeTests': None,
             'newCases': 0,
             'newDeaths': 0,
             'positiveTests': None,
             'vaccinationsCompleted': 4900,
             'vaccinationsInitiated': 5157,
             'vaccinationsInitiatedDemographics': None,
             'vaccinesAdministered': 10057,
             'vaccinesAdministeredDemographics': None,
             'vaccinesDistributed': None},
 'annotations': {'caseDensity': {'anomalies': [],
                          

In [4]:
# Iterate API
states_list = []
fips_list = []
county_list = []
populations = []
cases = []
vaccinations_Completed = []
vaccinations_Initiated = []
vaccinations_Administered = []

for x in covid_19_data:
    states_list.append(x['state'])  
    fips_list.append(x['fips'])  
    county_list.append(x['county']) 
    populations.append(x['population'])  
    cases.append(x['actuals']['cases'])
    vaccinations_Completed.append(x['actuals']['vaccinationsCompleted'])
    vaccinations_Initiated.append(x['actuals']['vaccinationsInitiated']) 
    vaccinations_Administered.append(x['actuals']['vaccinesAdministered'])

In [5]:
# Create dataframe
vaccination_df = pd.DataFrame({
    "State": states_list,
    "Fips" : fips_list,
    "County" : county_list,
    "Population": populations,
    "Total Current Cases" : cases,
    "Vaccination Completed" : vaccinations_Completed,
    "Vaccination Initiated" : vaccinations_Initiated,
    "Vaccination Administered" : vaccinations_Administered
})
vaccination_df.head()

State   Fips          County  Population  Total Current Cases  \
0    MI  26001   Alcona County       10405                  739   
1    MI  26003    Alger County        9108                  667   
2    MI  26005  Allegan County      118081                11154   
3    MI  26007   Alpena County       28405                 2268   
4    MI  26009   Antrim County       23324                 1632   

   Vaccination Completed  Vaccination Initiated  Vaccination Administered  
0                   4900                   5157                     10057  
1                   4509                   4950                      9459  
2                  45894                  50431                     96325  
3                  12675                  13355                     26030  
4                  10994                  11705                     22699

In [6]:
# Split Strig
vaccination_df['County'] = vaccination_df['County'].str.split(pat=" County", n=-1, expand=True)

vaccination_df

State   Fips     County  Population  Total Current Cases  \
0     MI  26001     Alcona       10405                  739   
1     MI  26003      Alger        9108                  667   
2     MI  26005    Allegan      118081                11154   
3     MI  26007     Alpena       28405                 2268   
4     MI  26009     Antrim       23324                 1632   
..   ...    ...        ...         ...                  ...   
78    MI  26157    Tuscola       52245                 5664   
79    MI  26159  Van Buren       75677                 7128   
80    MI  26161  Washtenaw      367601                27083   
81    MI  26163      Wayne     1749343               165350   
82    MI  26165    Wexford       33631                 2893   

    Vaccination Completed  Vaccination Initiated  Vaccination Administered  
0                    4900                   5157                     10057  
1                    4509                   4950                      9459  
2                   45894                  50431                     96325  
3                   12675                  13355                     26030  
4                   10994                  11705                     22699  
..                    ...                    ...                       ...  
78                  18908                  20511                     39419  
79                  30816                  34014                     64830  
80                 193089                 209895                    402984  
81                 661495                 768127                   1429622  
82                  13512                  14629                     28141  

[83 rows x 8 columns]

In [7]:
# Using .apply() fuction to get vaccinate completion rate
vaccination_df["Percent Completed"] = vaccination_df.apply(
    lambda x: x['Vaccination Completed']/x['Population'], axis =1) 

# Change formattingPo
format_dict = {'Percent Completed': '{:.1%}'}
vaccination_df.head().style.format(format_dict)

In [8]:
# Using .aggregate()
vaccination_MI = vaccination_df.groupby('State', as_index=True).agg({'Percent Completed': ['min', 'max']})
vaccination_MI

Percent Completed          
                    min       max
State                            
MI             0.239333  0.615091

In [9]:
# Max/min county
vaccination_df.sort_values(by=['Percent Completed'], ascending=False).style.format(format_dict)

In [10]:
# Pandas profile of MI covid data
mi_covid_data = vaccination_df.profile_report()
mi_covid_data

In [11]:
# Fatalities
fips_list_1 = []
deaths = []
infection_rate = []



for x in covid_19_data:
    fips_list_1.append(x['fips'])   
    deaths.append(x['actuals']['deaths'])
    infection_rate.append(x['metrics']['infectionRate'])
    
    
    
    
death_infection = pd.DataFrame({

    "Fips" : fips_list_1,
    "Deaths" : deaths,
    "Infection Rate": infection_rate
      
})




death_infection.head()

Fips  Deaths  Infection Rate
0  26001      32            1.00
1  26003       7            1.00
2  26005     156            0.56
3  26007      62            0.75
4  26009      29            0.84

In [12]:
# Positive-Test Ratio
fips_list_2 = []
test_postive_ratio  =[]
case_density =[]

for x in covid_19_data:
    fips_list_2.append(x['fips'])   
    test_postive_ratio.append(x['metrics']['testPositivityRatio'])
    case_density.append(x['metrics']['caseDensity'])
    
test_case_ratios = pd.DataFrame({

    "Fips" : fips_list_2,
    "Test Positive Ratio": test_postive_ratio,
    "Case Density": case_density
    
})


    
test_case_ratios.head()


Fips  Test Positive Ratio  Case Density
0  26001                0.007           1.4
1  26003                  NaN           0.0
2  26005                0.037           3.6
3  26007                0.021           3.5
4  26009                0.005           2.4

In [13]:
# Johns Hopkins CSV
covid_df=pd.read_csv(r'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_US.csv')

In [14]:
# MI data
original_mi_covid_df = covid_df.loc[covid_df['Province_State']=='Michigan']
original_mi_covid_df

UID iso2 iso3  code3     FIPS      Admin2 Province_State  \
1282  84026001   US  USA    840  26001.0      Alcona       Michigan   
1283  84026003   US  USA    840  26003.0       Alger       Michigan   
1284  84026005   US  USA    840  26005.0     Allegan       Michigan   
1285  84026007   US  USA    840  26007.0      Alpena       Michigan   
1286  84026009   US  USA    840  26009.0      Antrim       Michigan   
...        ...  ...  ...    ...      ...         ...            ...   
1364  84090026   US  USA    840  90026.0  Unassigned       Michigan   
1365  84026159   US  USA    840  26159.0   Van Buren       Michigan   
1366  84026161   US  USA    840  26161.0   Washtenaw       Michigan   
1367  84026163   US  USA    840  26163.0       Wayne       Michigan   
1368  84026165   US  USA    840  26165.0     Wexford       Michigan   

     Country_Region        Lat      Long_  ...  6/5/21  6/6/21  6/7/21  \
1282             US  44.684686 -83.595079  ...     738     738     738   
1283             US  46.412929 -86.602601  ...     515     515     516   
1284             US  42.591470 -85.891029  ...   11118   11118   11124   
1285             US  45.034777 -83.622124  ...    2262    2262    2262   
1286             US  44.996902 -85.155031  ...    1627    1627    1627   
...             ...        ...        ...  ...     ...     ...     ...   
1364             US   0.000000   0.000000  ...      22      22      20   
1365             US  42.251902 -86.019391  ...    7109    7109    7112   
1366             US  42.253105 -83.838532  ...   26404   26404   26412   
1367             US  42.280984 -83.281255  ...  164769  164769  164860   
1368             US  44.338536 -85.577127  ...    2887    2887    2887   

      6/8/21  6/9/21  6/10/21  6/11/21  6/12/21  6/13/21  6/14/21  
1282     739     739      739      739      739      739      739  
1283     516     516      516      516      516      516      516  
1284   11134   11135    11146    11149    11151    11151    11154  
1285    2263    2266     2265     2266     2266     2266     2268  
1286    1628    1628     1629     1630     1630     1630     1631  
...      ...     ...      ...      ...      ...      ...      ...  
1364      20      20       20       20       21       21       21  
1365    7118    7120     7121     7125     7125     7125     7128  
1366   26419   26420    26428    26432    26439    26439    26448  
1367  164937  165000   165056   165146   165215   165215   165293  
1368    2887    2888     2889     2890     2890     2890     2893  

[87 rows x 521 columns]

In [15]:
#Drop columns
mi_covid_df = original_mi_covid_df.drop(original_mi_covid_df.iloc[:,:4], axis=1)
mi_covid_df = mi_covid_df.drop(labels= ['Country_Region','Lat','Long_','Combined_Key'], axis=1)

# Rename columns
mi_covid_df = mi_covid_df.rename(columns={'Admin2': 'County', 'Province_State':'State'})

# Reset index
mi_covid_df = mi_covid_df.reset_index(drop=True)

mi_covid_df

FIPS      County     State  1/22/20  1/23/20  1/24/20  1/25/20  \
0   26001.0      Alcona  Michigan        0        0        0        0   
1   26003.0       Alger  Michigan        0        0        0        0   
2   26005.0     Allegan  Michigan        0        0        0        0   
3   26007.0      Alpena  Michigan        0        0        0        0   
4   26009.0      Antrim  Michigan        0        0        0        0   
..      ...         ...       ...      ...      ...      ...      ...   
82  90026.0  Unassigned  Michigan        0        0        0        0   
83  26159.0   Van Buren  Michigan        0        0        0        0   
84  26161.0   Washtenaw  Michigan        0        0        0        0   
85  26163.0       Wayne  Michigan        0        0        0        0   
86  26165.0     Wexford  Michigan        0        0        0        0   

    1/26/20  1/27/20  1/28/20  ...  6/5/21  6/6/21  6/7/21  6/8/21  6/9/21  \
0         0        0        0  ...     738     738     738     739     739   
1         0        0        0  ...     515     515     516     516     516   
2         0        0        0  ...   11118   11118   11124   11134   11135   
3         0        0        0  ...    2262    2262    2262    2263    2266   
4         0        0        0  ...    1627    1627    1627    1628    1628   
..      ...      ...      ...  ...     ...     ...     ...     ...     ...   
82        0        0        0  ...      22      22      20      20      20   
83        0        0        0  ...    7109    7109    7112    7118    7120   
84        0        0        0  ...   26404   26404   26412   26419   26420   
85        0        0        0  ...  164769  164769  164860  164937  165000   
86        0        0        0  ...    2887    2887    2887    2887    2888   

    6/10/21  6/11/21  6/12/21  6/13/21  6/14/21  
0       739      739      739      739      739  
1       516      516      516      516      516  
2     11146    11149    11151    11151    11154  
3      2265     2266     2266     2266     2268  
4      1629     1630     1630     1630     1631  
..      ...      ...      ...      ...      ...  
82       20       20       21       21       21  
83     7121     7125     7125     7125     7128  
84    26428    26432    26439    26439    26448  
85   165056   165146   165215   165215   165293  
86     2889     2890     2890     2890     2893  

[87 rows x 513 columns]

In [16]:
# Cases by date for MI
mi_date_df = mi_covid_df.groupby('State').sum()
mi_date_df = mi_date_df.drop(labels=['FIPS'], axis=1)
mi_date_df = mi_date_df.transpose()
mi_date_df = mi_date_df.rename_axis(None, axis=1)
mi_date_df = mi_date_df.reset_index(drop=False)
mi_date_df = mi_date_df.rename(columns={'Michigan':'Cases','index':'Date'})

mi_date_df

Date   Cases
0    1/22/20       0
1    1/23/20       0
2    1/24/20       0
3    1/25/20       0
4    1/26/20       0
..       ...     ...
505  6/10/21  996427
506  6/11/21  996756
507  6/12/21  996986
508  6/13/21  996986
509  6/14/21  997375

[510 rows x 2 columns]

In [17]:
# Aggregate cases per county
county_cases_df = mi_covid_df.drop(labels=['State'], axis=1)
county_cases_df = county_cases_df.groupby(['FIPS','County']).sum()
county_cases_df = county_cases_df.agg(['sum','mean','max'], axis=1)
county_cases_df = county_cases_df.reset_index()
county_cases_df = county_cases_df.rename(columns={'level_0':'FIPS','level_1':'County','sum':'Total Cases','mean':'Daily Average Cases','max':'Highest Single-Day Cases'})

county_cases_df

FIPS      County  Total Cases  Daily Average Cases  \
0   26001.0      Alcona     106290.0           208.411765   
1   26003.0       Alger      91724.0           179.850980   
2   26005.0     Allegan    1750044.0          3431.458824   
3   26007.0      Alpena     349727.0           685.739216   
4   26009.0      Antrim     228888.0           448.800000   
..      ...         ...          ...                  ...   
80  26161.0   Washtenaw    4583169.0          8986.605882   
81  26163.0       Wayne   29928562.0         58683.454902   
82  26165.0     Wexford     379916.0           744.933333   
83  80026.0   Out of MI     389337.0           763.405882   
84  90026.0  Unassigned      10838.0            21.250980   

    Highest Single-Day Cases  
0                      739.0  
1                      516.0  
2                    11154.0  
3                     2268.0  
4                     1631.0  
..                       ...  
80                   26448.0  
81                  165293.0  
82                    2893.0  
83                    2890.0  
84                     409.0  

[85 rows x 5 columns]

In [18]:
# Creates new DF with just county and dates
prep_unpivot_df = mi_covid_df.drop(labels=['FIPS','State'], axis=1)
prep_unpivot_df.head()

County  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  \
0   Alcona        0        0        0        0        0        0        0   
1    Alger        0        0        0        0        0        0        0   
2  Allegan        0        0        0        0        0        0        0   
3   Alpena        0        0        0        0        0        0        0   
4   Antrim        0        0        0        0        0        0        0   

   1/29/20  1/30/20  ...  6/5/21  6/6/21  6/7/21  6/8/21  6/9/21  6/10/21  \
0        0        0  ...     738     738     738     739     739      739   
1        0        0  ...     515     515     516     516     516      516   
2        0        0  ...   11118   11118   11124   11134   11135    11146   
3        0        0  ...    2262    2262    2262    2263    2266     2265   
4        0        0  ...    1627    1627    1627    1628    1628     1629   

   6/11/21  6/12/21  6/13/21  6/14/21  
0      739      739      739      739  
1      516      516      516      516  
2    11149    11151    11151    11154  
3     2266     2266     2266     2268  
4     1630     1630     1630     1631  

[5 rows x 511 columns]

In [19]:
# TRANSFORMATION 1 - uses pd.melt - unpivots to transpose date columns to rows by county

# TABLE cases_by_date_table
df_unpivoted = prep_unpivot_df.melt(id_vars=['County'], var_name='Date', value_name='Cases')
df_unpivoted

County     Date   Cases
0          Alcona  1/22/20       0
1           Alger  1/22/20       0
2         Allegan  1/22/20       0
3          Alpena  1/22/20       0
4          Antrim  1/22/20       0
...           ...      ...     ...
44365  Unassigned  6/14/21      21
44366   Van Buren  6/14/21    7128
44367   Washtenaw  6/14/21   26448
44368       Wayne  6/14/21  165293
44369     Wexford  6/14/21    2893

[44370 rows x 3 columns]

In [20]:
# wayne_top_df

'''TRANSFORMATION 2 - uses df.nlargest, df.loc, df.diff - identifies which county has the most daily cases then dive deeper and find the 
largest changes from one day to the next'''
# Displays county, dates, and cases with largest case counts
top_df = df_unpivoted.nlargest(50, 'Cases', keep='first')
#top_df
# Confirmed - it was Wayne county
# Now dive deeper - top 10 largest instances of daily change from one day to the next 
wayne_df = df_unpivoted.loc[df_unpivoted['County']=='Wayne']
wayne_df = wayne_df.set_index('County')
wayne_df['Daily Change in Cases'] = wayne_df['Cases'].diff()
wayne_top_df = wayne_df.nlargest(10, 'Daily Change in Cases', keep='first')
wayne_top_df['Percent Change'] = wayne_top_df['Cases'].pct_change().astype(float).map("{:.2%}".format)
wayne_top_df['Percent Change'].replace({"nan%": 0},inplace=True)

wayne_top_df

Date   Cases  Daily Change in Cases Percent Change
County                                                        
Wayne     4/5/21  125364                 2393.0              0
Wayne   11/27/20   62273                 2368.0        -50.33%
Wayne    4/13/21  137370                 2123.0        120.59%
Wayne    4/12/21  135247                 2078.0         -1.55%
Wayne     4/7/21  128394                 1864.0         -5.07%
Wayne     4/3/21  122971                 1846.0         -4.22%
Wayne    3/29/21  116612                 1801.0         -5.17%
Wayne    4/16/21  142075                 1751.0         21.84%
Wayne    4/19/21  144922                 1705.0          2.00%
Wayne     4/9/21  131774                 1699.0         -9.07%

In [21]:
# Pandas profile 
mi_covid_profile = df_unpivoted.profile_report()
mi_covid_profile

In [22]:
# cases_by_month_table

# TRANSFORMATION 5 - converts date to month, then evaluates cases by month overall per county
# Check out column data types 
# df_unpivoted.info()
# Split date by "/" delimiter
#split = df_unpivoted['Date'].str.split("/", n=2, expand=True)

df_unpivoted[['Month','Day','Year']] = df_unpivoted['Date'].str.split("/", expand = True)

df_unpivoted = df_unpivoted.loc[df_unpivoted['Month']=='4']
df_unpivoted

month_dict = {
    '4': 'April'   
}

for index,row in df_unpivoted.iterrows():
        df_1 = df_unpivoted.replace({"Month": month_dict})
april_df = df_1

april_df

County     Date   Cases  Month Day Year
6090       Alcona   4/1/20       0  April   1   20
6091        Alger   4/1/20       0  April   1   20
6092      Allegan   4/1/20       5  April   1   20
6093       Alpena   4/1/20       0  April   1   20
6094       Antrim   4/1/20       5  April   1   20
...           ...      ...     ...    ...  ..  ...
40450  Unassigned  4/30/21      24  April  30   21
40451   Van Buren  4/30/21    6718  April  30   21
40452   Washtenaw  4/30/21   25372  April  30   21
40453       Wayne  4/30/21  154782  April  30   21
40454     Wexford  4/30/21    2687  April  30   21

[5220 rows x 6 columns]

In [23]:
# april_2020_and_2021_table

df_1["Month_Year"] = df_1["Month"] + " 20" + df_1["Year"]
df_1
new_df = df_1.sort_values('County')
new_df

new_df = new_df.drop(labels= ['Date','Month','Day','Year'], axis=1)
new_df = new_df.groupby(['County', "Month_Year"]).sum()["Cases"]
new_df = new_df.reset_index()
new_df = new_df[new_df["Month_Year"]== "April 2021"]
year_comparison_df = new_df

year_comparison_df

County  Month_Year    Cases
1        Alcona  April 2021    18216
3         Alger  April 2021    14300
5       Allegan  April 2021   281281
7        Alpena  April 2021    55521
9        Antrim  April 2021    41832
..          ...         ...      ...
165  Unassigned  April 2021      695
167   Van Buren  April 2021   185917
169   Washtenaw  April 2021   706118
171       Wayne  April 2021  4178863
173     Wexford  April 2021    72614

[87 rows x 3 columns]

In [24]:
# Connect to postresql
engine = create_engine(f'postgresql+psycopg2://{username}:{password}@{host}:{port}/{database}')
session = Session(engine)

In [25]:
engine.table_names()

[]

In [26]:
# Create tables
vaccination_df.to_sql(name='vaccination', con=engine, if_exists='replace', index=False)

In [27]:
pd.read_sql_query('select * from vaccination', con=engine).head()

State   Fips   County  Population  Total Current Cases  \
0    MI  26001   Alcona       10405                  739   
1    MI  26003    Alger        9108                  667   
2    MI  26005  Allegan      118081                11154   
3    MI  26007   Alpena       28405                 2268   
4    MI  26009   Antrim       23324                 1632   

   Vaccination Completed  Vaccination Initiated  Vaccination Administered  \
0                   4900                   5157                     10057   
1                   4509                   4950                      9459   
2                  45894                  50431                     96325   
3                  12675                  13355                     26030   
4                  10994                  11705                     22699   

   Percent Completed  
0           0.470927  
1           0.495059  
2           0.388665  
3           0.446224  
4           0.471360

In [28]:
death_infection.to_sql(name='death_infections', con=engine, if_exists='replace', index=False)

In [29]:
pd.read_sql_query('select * from death_infections', con=engine).head()

Fips  Deaths  Infection Rate
0  26001      32            1.00
1  26003       7            1.00
2  26005     156            0.56
3  26007      62            0.75
4  26009      29            0.84

In [30]:
test_case_ratios.to_sql(name='test_case_ratios', con=engine, if_exists='replace', index=False)

In [31]:
pd.read_sql_query('select * from test_case_ratios', con=engine).head()

Fips  Test Positive Ratio  Case Density
0  26001                0.007           1.4
1  26003                  NaN           0.0
2  26005                0.037           3.6
3  26007                0.021           3.5
4  26009                0.005           2.4

In [32]:
year_comparison_df.to_sql(name='april_2020_2021', con=engine, if_exists='replace', index=False)

In [33]:
pd.read_sql_query('select * from april_2020_2021', con=engine).head()

County  Month_Year   Cases
0   Alcona  April 2021   18216
1    Alger  April 2021   14300
2  Allegan  April 2021  281281
3   Alpena  April 2021   55521
4   Antrim  April 2021   41832

In [34]:
county_cases_df.to_sql(name='Cases by County', con=engine, if_exists='replace', index=False)

In [35]:
pd.read_sql_query('select * from "Cases by County"', con=engine)

FIPS      County  Total Cases  Daily Average Cases  \
0   26001.0      Alcona     106290.0           208.411765   
1   26003.0       Alger      91724.0           179.850980   
2   26005.0     Allegan    1750044.0          3431.458824   
3   26007.0      Alpena     349727.0           685.739216   
4   26009.0      Antrim     228888.0           448.800000   
..      ...         ...          ...                  ...   
80  26161.0   Washtenaw    4583169.0          8986.605882   
81  26163.0       Wayne   29928562.0         58683.454902   
82  26165.0     Wexford     379916.0           744.933333   
83  80026.0   Out of MI     389337.0           763.405882   
84  90026.0  Unassigned      10838.0            21.250980   

    Highest Single-Day Cases  
0                      739.0  
1                      516.0  
2                    11154.0  
3                     2268.0  
4                     1631.0  
..                       ...  
80                   26448.0  
81                  165293.0  
82                    2893.0  
83                    2890.0  
84                     409.0  

[85 rows x 5 columns]

In [36]:
engine.table_names()

['vaccination',
 'death_infections',
 'test_case_ratios',
 'april_2020_2021',
 'Cases by County']

In [37]:
# End session
session.close()